In [1]:
import hvplot.xarray
import intake
import pandas as pd
import xarray as xr
from distributed import Client
from ncar_jobqueue import NCARCluster

In [2]:
cluster = NCARCluster()
cluster.adapt(minimum_jobs=2, maximum_jobs=5)
client = Client(cluster)
cluster

## Reynolds optimally interpolated sea surface temperature (OISST) data

In [3]:
cat = intake.open_catalog("../catalogs/obs.yaml")
cat

obs:
  args:
    path: ../catalogs/obs.yaml
  description: ''
  driver: intake.catalog.local.YAMLFileCatalog
  metadata: {}


In [4]:
list(cat)

['sst_oi_bulk']

In [5]:
cat.sst_oi_bulk

sst_oi_bulk:
  args:
    chunks: {}
    storage_options:
      simplecache:
        same_names: true
    urlpath: simplecache::https://www.ncei.noaa.gov/thredds/fileServer/OisstBase/NetCDF/V2.1/AVHRR/201001/oisst-avhrr-v02r01.20100101.nc
    xarray_kwargs:
      decode_times: true
  description: Optimum Interpolation Sea Surface Temperature (OISST) v2.1 provided
    by the NOAA/NCEI from their Web site at https://www.ncdc.noaa.gov/oisst/data-access
  driver: intake_xarray.netcdf.NetCDFSource
  metadata:
    catalog_dir: /glade/work/abanihi/devel/andersy005/intake-tutorial/notebooks/../catalogs/


In [6]:
%%time
ds = cat.sst_oi_bulk(year=2000, month=7, day=5).to_dask()
ds

CPU times: user 41.9 ms, sys: 12.4 ms, total: 54.3 ms
Wall time: 618 ms


<xarray.Dataset>
Dimensions:  (lat: 720, lon: 1440, time: 1, zlev: 1)
Coordinates:
  * lat      (lat) float32 -89.88 -89.62 -89.38 -89.12 ... 89.38 89.62 89.88
  * lon      (lon) float32 0.125 0.375 0.625 0.875 ... 359.1 359.4 359.6 359.9
  * time     (time) datetime64[ns] 2000-07-05T12:00:00
  * zlev     (zlev) float32 0.0
Data variables:
    anom     (time, zlev, lat, lon) float32 dask.array<chunksize=(1, 1, 720, 1440), meta=np.ndarray>
    err      (time, zlev, lat, lon) float32 dask.array<chunksize=(1, 1, 720, 1440), meta=np.ndarray>
    ice      (time, zlev, lat, lon) float32 dask.array<chunksize=(1, 1, 720, 1440), meta=np.ndarray>
    sst      (time, zlev, lat, lon) float32 dask.array<chunksize=(1, 1, 720, 1440), meta=np.ndarray>
Attributes: (12/37)
    title:                      NOAA/NCEI 1/4 Degree Daily Optimum Interpolat...
    source:                     ICOADS, NCEP_GTS, GSFC_ICE, NCEP_ICE, Pathfin...
    id:                         oisst-avhrr-v02r01.20000705.nc
    naming_authority:           gov.noaa.ncei
    summary:                    NOAAs 1/4-degree Daily Optimum Interpolation ...
    cdm_data_type:              Grid
    ...                         ...
    metadata_link:              https://doi.org/10.25921/RE9P-PT57
    ncei_template_version:      NCEI_NetCDF_Grid_Template_v2.0
    comment:                    Data was converted from NetCDF-3 to NetCDF-4 ...
    sensor:                     Thermometer, AVHRR
    Conventions:                CF-1.6, ACDD-1.3
    references:                 Reynolds, et al.(2007) Daily High-Resolution-...

In [7]:
date_range = pd.date_range(start='2020-05-01', end='2020-07-01')


def retrieve_dataset(value):
    try:
        ds = cat.sst_oi_bulk(year=value.year, month=value.month, day=value.day).to_dask()
    except Exception:
        ds = None
    return ds


datasets = client.map(retrieve_dataset, date_range)
datasets = client.gather(datasets)
datasets = [dataset for dataset in datasets if dataset is not None]
ds = xr.concat(datasets, dim='time', compat='override', coords='minimal').squeeze()
ds

<xarray.Dataset>
Dimensions:  (lat: 720, lon: 1440, time: 62)
Coordinates:
  * time     (time) datetime64[ns] 2020-05-01T12:00:00 ... 2020-07-01T12:00:00
    zlev     float32 0.0
  * lat      (lat) float32 -89.88 -89.62 -89.38 -89.12 ... 89.38 89.62 89.88
  * lon      (lon) float32 0.125 0.375 0.625 0.875 ... 359.1 359.4 359.6 359.9
Data variables:
    sst      (time, lat, lon) float32 dask.array<chunksize=(1, 720, 1440), meta=np.ndarray>
    anom     (time, lat, lon) float32 dask.array<chunksize=(1, 720, 1440), meta=np.ndarray>
    err      (time, lat, lon) float32 dask.array<chunksize=(1, 720, 1440), meta=np.ndarray>
    ice      (time, lat, lon) float32 dask.array<chunksize=(1, 720, 1440), meta=np.ndarray>
Attributes: (12/37)
    Conventions:                CF-1.6, ACDD-1.3
    title:                      NOAA/NCEI 1/4 Degree Daily Optimum Interpolat...
    references:                 Reynolds, et al.(2007) Daily High-Resolution-...
    source:                     ICOADS, NCEP_GTS, GSFC_ICE, NCEP_ICE, Pathfin...
    id:                         oisst-avhrr-v02r01.20200501.nc
    naming_authority:           gov.noaa.ncei
    ...                         ...
    time_coverage_start:        2020-05-01T00:00:00Z
    time_coverage_end:          2020-05-01T23:59:59Z
    metadata_link:              https://doi.org/10.25921/RE9P-PT57
    ncei_template_version:      NCEI_NetCDF_Grid_Template_v2.0
    comment:                    Data was converted from NetCDF-3 to NetCDF-4 ...
    sensor:                     Thermometer, AVHRR

In [8]:
width = 800
height = 400
widget_type = 'scrubber'
widget_location = 'bottom'
rasterize = True

sst = ds.sst.hvplot(
    x='lon',
    y='lat',
    cmap='RdBu_r',
    width=width,
    height=height,
    rasterize=rasterize,
    widget_type=widget_type,
    widget_location=widget_location,
    attr_labels=False,
)
sst

Column
    [0] HoloViews(DynamicMap, widget_location='bottom', widget_type='scrubber')
    [1] Row
        [0] HSpacer()
        [1] WidgetBox
            [0] Player(end=61, width=550)
        [2] HSpacer()